In [41]:
import pandas as pd
import numpy as np
import pickle
import Bio   
import plotly.express as px
import plotly.graph_objects as go
from jproperties import Properties
#import wandb
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline, AutoModel, TrainingArguments, Trainer
from motif_utils import seq2kmer # Soruced from https://github.com/jerryji1993/DNABERT
import torch
from datasets import Dataset
import evaluate
import json
from load_data import create_dataset, explode_dna
import wandb

from transformers.onnx import FeaturesManager
import transformers
from pathlib import Path
from sklearn.preprocessing import StandardScaler,MinMaxScaler

In [2]:
'''
1. Normalize dataset
2. Try with smaller networks?
3. Try with very few training examples to try and get overfitting
4. Expand model size
5. Hyper Param Search https://huggingface.co/blog/ray-tune

'''

'\n1. Normalize dataset\n2. Try with smaller networks?\n3. Try with very few training examples to try and get overfitting\n4. Expand model size\n5. Hyper Param Search https://huggingface.co/blog/ray-tune\n\n'

In [3]:
#train, val, test = create_dataset()

In [6]:
with open("./data/gene_symbol_dna_sequence.pkl", 'rb') as file:
        gene =  pickle.load(file)
        
with open("./data/capstone_body_weight_Statistical_effect_size_analysis_genotype_early_adult_scaled_13022023_gene_symbol_harmonized.pkl", 'rb') as file:
        effect =  pickle.load(file)
        
        
with open("./data/gene_symbol_dna_sequence_exon.pkl", 'rb') as file:
        exon =  pickle.load(file)
        

In [8]:
gene

Gene stable ID      Gene name  \
0      ENSMUSG00000064336          mt-Tf   
1      ENSMUSG00000064337        mt-Rnr1   
2      ENSMUSG00000064338          mt-Tv   
3      ENSMUSG00000064339        mt-Rnr2   
4      ENSMUSG00000064340         mt-Tl1   
...                   ...            ...   
57005  ENSMUSG00000089575        Gm23005   
57006  ENSMUSG00000119806        Gm24077   
57007  ENSMUSG00000087609  4930442J19Rik   
57008  ENSMUSG00000119525        Gm23261   
57009  ENSMUSG00000083391        Gm14148   

                                                Sequence  
0      GTTAATGTAGCTTAATAACAAAGCAAAGCACTGAAAATGCTTAGAT...  
1      AAAGGTTTGGTCCTGGCCTTATAATTAATTAGAGGTAAAATTACAC...  
2      CATAGTGTAGCTTAATATTAAAGCATCTGGCCTACACCCAGAAGAT...  
3      ACTAATCCTAGCCCTAGCCCTACACAAATATAATTATACTATTATA...  
4      ATTAGGGTGGCAGAGCCAGGAAATTGCGTAAGACTTAAAACCTTGT...  
...                                                  ...  
57005  TCTACACCTAGAGGCATTGTTGCTTTGGCTCTGTGTTCCATGTGTA...  
57006  CCTACACCTAGAGGCATTGTAGCTTTGGCTCTGTGTTCCATGTGTA...  
57007  TTGCTCCTGCGCAAAGGCCTCTGGTTGAAGCCGTTGGTGGGCAGTG...  
57008  CCTACCCCTAGAGGCATTGTAGCTTTGGCTCTGTGTTCCATGTGTA...  
57009  ATGGTGAAGGTCGGTGTGAACGGATTTGGCCGAATTGGGCGCCTGG...  

[57010 rows x 3 columns]

In [16]:

fig = go.Figure()
fig.add_trace(go.Histogram(x = exon.Sequence.str.len()))
fig.add_trace(go.Histogram(x = gene.Sequence.str.len()))
fig.show()

In [18]:
len(exon[exon.Sequence.str.len() <= 512])/len(exon)

0.8525210880661435

In [14]:
exon.Sequence.str.len()

0           68
1          955
2           69
3         1582
4           75
          ... 
537977     178
537978     174
537979     136
537980     513
537981     495
Name: Sequence, Length: 537982, dtype: int64

In [21]:
exon.columns
trimmed = exon[exon.Sequence.str.len() <= 512].copy()

In [23]:
effect = effect[['gene_symbol','est_f_ea','p_f_ea']].copy()
final = pd.merge(effect, trimmed, left_on="gene_symbol", right_on="Gene name")

In [45]:
def data_clean(df, size = None):
    if size:
        df = df.copy().sample(frac=1)[:size]
    
    
    df_len = len(df)
    df = df.rename({"Sequence":"dna_seq", "est_f_ea":"label"}, axis=1)
    df.dna_seq = df.dna_seq.astype(str)
    df = df.sample(frac=1)
    train = df[:int(np.round(df_len*.8))].copy()
    val = df[int(np.round(df_len*.8)):int(np.round(df_len*.9))].copy()
    test = df[int(np.round(df_len*.9)):].copy()

    scaler = MinMaxScaler((-1,1))
    scaler.fit(train["label"].values.reshape(-1, 1))
    train["label"] = scaler.transform(train["label"].values.reshape(-1, 1))
    val["label"] = scaler.transform(val["label"].values.reshape(-1, 1))
    test["label"] = scaler.transform(test["label"].values.reshape(-1, 1))
    
    return train, val, test
    
train, val, test = data_clean(final, 10)

In [46]:
train

gene_symbol     label    p_f_ea      Gene stable ID  Gene name  \
42511        Fnip2  1.000000  0.000047  ENSMUSG00000061175      Fnip2   
92594       Slc2a7 -0.330045  0.797015  ENSMUSG00000062064     Slc2a7   
100782       Tead3 -0.295200  0.984035  ENSMUSG00000002249      Tead3   
18745    Catspere2  0.287890  0.020033  ENSMUSG00000091476  Catspere2   
48277       Hectd2 -0.489218  0.385645  ENSMUSG00000041180     Hectd2   
50562        Ifi44 -1.000000  0.001937  ENSMUSG00000028037      Ifi44   
20936     Cdc42bpg -0.799902  0.005308  ENSMUSG00000024769   Cdc42bpg   
113712     Zfp385b -0.549352  0.244787  ENSMUSG00000027016    Zfp385b   

            Exon stable ID                                            dna_seq  
42511   ENSMUSE00001271256  GTCTCAGAGCACCAGCAAGGCAAATGTTAGAAATTTTGGCCGCTCA...  
92594   ENSMUSE00000667091  ATGGAGGACAAAGAGATAGGGACACCTCTGCCCTTGCCACACTCGG...  
100782  ENSMUSE00001261296  GTCGAAATGAGCTGATTGCCCGCTACATCAAGCTGAGGACTGGAAA...  
18745   ENSMUSE00001339123                          AGACGTTTATTACAACTTAAGCCAG  
48277   ENSMUSE00001284300  TGAGAGACCTACCACCAATTTGTCTTGATGTTAGACAAAAACAGCG...  
50562   ENSMUSE00001214648  TTCGATTCCATGAAACCAATCACATCAAACCATCCGAACTATACCC...  
20936   ENSMUSE00000233104  CCTGTGGCTACTTCTGTCACTCAGCTTGTGCGTCACAAGCCCCACC...  
113712  ENSMUSE00000833752  TAACAGAGAAGAATAGAAATCAATAGTGGTGGACAATCTCTTCCCA...

In [47]:
def show_dist():
    fig = go.Figure()
    fig.add_trace(go.Histogram(x = val["label"], histnorm='probability', name = "val"))
    fig.add_trace(go.Histogram(x = test["label"], histnorm='probability', name = "test"))
    fig.add_trace(go.Histogram(x = train["label"], histnorm='probability', name = "train"))
    
    fig.update_layout(
        barmode="overlay",
        bargap=0.1)
    fig.show()
show_dist()

In [50]:
train_mean = train.label.mean()
val_mean = val.label.mean()
test_mean = test.label.mean()

print(f"Train: {test_mean}, Val: {val_mean}, Test: {test_mean}")

Train: 0.02670356784813932, Val: -0.09640399715057177, Test: 0.02670356784813932


In [51]:
tokenizer = AutoTokenizer.from_pretrained('zhihan1996/DNA_bert_6')
def tokenize_function(df):
    return tokenizer(df["dna_seq"], padding=True, truncation=True, max_length=512)#512


train = Dataset.from_pandas(train).map(tokenize_function, batched=True)
val = Dataset.from_pandas(val).map(tokenize_function, batched=True)
test = Dataset.from_pandas(test).map(tokenize_function, batched=True)

100%|██████████| 1/1 [00:00<00:00, 333.28ba/s]


In [52]:

model = AutoModelForSequenceClassification.from_pretrained('zhihan1996/DNA_bert_6',
                                                           num_labels=1, 
                                                           ignore_mismatched_sizes=True).to("cuda")
wandb.init(project="DNA-Weight", entity="pcoady")
wandb_config = wandb.config


def visualize_model():
        feature = "sequence-classification"
        model_kind, model_onnx_config = FeaturesManager.check_supported_model_or_raise(model, feature=feature)
        onnx_config = model_onnx_config(model.config)
        onnx_inputs, onnx_outputs = transformers.onnx.export(
                preprocessor=tokenizer,
                model=model,
                config=onnx_config,
                opset=13,
                output=Path("pretrained-model.onnx")
        )


Some weights of the model checkpoint at zhihan1996/DNA_bert_6 were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.decoder.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at zhihan1996/DNA_bert_6 a

In [53]:
#evaluate.list_evaluation_modules()

In [54]:
mse_metric = evaluate.load("mse")
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    #labels = labels.reshape(-1, 1)
    baseline = np.array([val_mean for x in range(len(labels))])
    new_logits = logits.reshape(1,-1)[0]
    
    wandb.log({'Base Line': mse_metric.compute(predictions=baseline, references=labels)})
    wandb.log({'True Values': labels })
    wandb.log({'Predicted Values': new_logits})

    mse = mse_metric.compute(predictions=new_logits, references=labels)
    return mse

In [55]:
training_args = TrainingArguments(output_dir='weight_model', 
                                  evaluation_strategy='epoch',
                                  per_device_train_batch_size = 5,  
                                  num_train_epochs=1000)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train,
    eval_dataset=train,#CHANGED
    compute_metrics=compute_metrics
)

In [56]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol. If Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
c:\Users\zeusg\Envs\real-fast\lib\site-packages\transformers\optimization.py:306: FutureWarning:

This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning

***** Running training *****
  Num examples = 8
  Num Epochs = 1000
  Instantaneous batch size per device = 5
  Total train batch size (w. parallel, distributed & accumulation) = 5
  Gradient Accumulation steps = 1
  Total optimization steps = 2000
Automatic Weights & B

{'eval_loss': 0.35865461826324463, 'eval_mse': 0.35865463885098703, 'eval_runtime': 0.078, 'eval_samples_per_second': 102.504, 'eval_steps_per_second': 12.813, 'epoch': 1.0}


***** Running Evaluation *****
  Num examples = 8
  Batch size = 8
                                                  
  0%|          | 5/2000 [00:08<35:39,  1.07s/it]  The following columns in the evaluation set don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol. If Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.


{'eval_loss': 0.3649406433105469, 'eval_mse': 0.3649406496698322, 'eval_runtime': 0.0527, 'eval_samples_per_second': 151.761, 'eval_steps_per_second': 18.97, 'epoch': 2.0}


***** Running Evaluation *****
  Num examples = 8
  Batch size = 8
                                                
  0%|          | 7/2000 [00:08<22:17,  1.49it/s]

...

***** Running Evaluation *****
  Num examples = 8
  Batch size = 8
                                                  
 31%|███       | 623/2000 [01:32<02:55,  7.83it/s]

{'eval_loss': 0.36610618233680725, 'eval_mse': 0.36610617663616174, 'eval_runtime': 0.0459, 'eval_samples_per_second': 174.267, 'eval_steps_per_second': 21.783, 'epoch': 311.0}


 31%|███       | 624/2000 [01:33<02:48,  8.14it/s]The following columns in the evaluation set don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol. If Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8
  Batch size = 8
                                                  
 31%|███       | 624/2000 [01:33<02:48,  8.14it/s]

{'eval_loss': 0.35863441228866577, 'eval_mse': 0.3586344259818237, 'eval_runtime': 0.0451, 'eval_samples_per_second': 177.493, 'eval_steps_per_second': 22.187, 'epoch': 312.0}


KeyboardInterrupt: 

In [57]:
results = trainer.predict(train)
fig = go.Figure()
fig.add_trace(go.Histogram(x=results[1], histnorm='probability', name = "actual"))
fig.add_trace(go.Histogram(x=results[0].reshape(-1, 1)[:,0], histnorm='probability', name = "predictions"))

fig.update_layout(
    barmode="overlay",
    bargap=0.1)


fig.show()

The following columns in the test set don't have a corresponding argument in `BertForSequenceClassification.forward` and have been ignored: Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol. If Exon stable ID, Gene stable ID, p_f_ea, dna_seq, __index_level_0__, Gene name, gene_symbol are not expected by `BertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 8
  Batch size = 8


In [58]:
results[0]

array([[-0.26117468],
       [-0.26117468],
       [-0.26117468],
       [-0.26117468],
       [-0.26117468],
       [-0.26117468],
       [-0.26117468],
       [-0.26117468]], dtype=float32)

In [ ]:
results[1]

In [ ]:
results[0]

In [ ]:
val_mean